In [ ]:
# This will be the notebook we use for our final visualization
import pandas as pd
import altair as alt
import numpy as np
# Texas Map Library
!pip install geopandas
import geopandas as gpd

# Increase max row
alt.data_transformers.enable('default', max_rows=6000)

DataTransformerRegistry.enable('default')

In [ ]:
# Interactive Texas Map and Housing Costs/Personal Income Line Graph
# load data
df = pd.read_excel("/Map+Unemployment.xlsx")
# change to str to allow transform_lookup
df['gid'] = df['gid'].astype('str')

# load texas counties map
counties = gpd.read_file('/texas.geojson')
from shapely.ops import orient
# simplify map to reduce lag when selecting & load times
counties.geometry = counties.geometry.simplify(0.05)
counties.geometry = counties.geometry.apply(orient, args=(-1,))

# county selector
select_county = alt.selection_multi(fields=['County Name'], empty= 'none')

# only use needed data
df_map = df[['Time','Growth Diff', 'gid']]
# remove 2000 and 2020 since income data is missing
df_map = df[(df['Time'] > 2000) & (df['Time'] < 2020)]

# Colored layer
texas_map = alt.Chart(counties).transform_lookup(
    # match with df_map['gid']
    lookup = 'gid',
    # copy required field
    from_ = alt.LookupData(data = df_map, key = 'gid', fields = ['Time', 'Growth Diff', 'County Name', '2020 Population'])
).mark_geoshape(stroke="darkgray").encode(
    # color according to mean_diff
    # selected color
    color = alt.condition(select_county, alt.value('orange'), alt.Color( 'Income_minus_HPI:Q', title = 'Income - HPI',
                                                                     scale=alt.Scale(scheme=alt.SchemeParams(name='redblue')) )),
    tooltip = ['County Name:N', '2020 Population:Q', 'Income_minus_HPI:Q']
).transform_aggregate(
    # need to transform to make mean(Growth Diff) preserve geometry and type data
    Income_minus_HPI = 'mean(Growth Diff):Q',
    # keep data used for tooltip (works since these data are the same per county)
    groupby = ["type", "gid", "geometry", "County Name", '2020 Population']
).add_selection(
    # add county selection
    select_county
).properties(
    width=900, height=700, title = 'Average Difference in Income and Housing Price Index Growth'
)

# create base for line graph
base = alt.Chart(df).encode(
    y = alt.Y('Growth Diff:Q', title = 'Percentage Difference'),
    x = alt.X('Time:Q', title = 'Year',
              # remove coma in year format
              axis = alt.Axis(format = 'd'),
              scale = alt.Scale(domain = [2000,2020])),
    color = alt.Color('County Name')
).properties(
    title = "Difference in Income and HPI Growth"
).transform_filter(
    # selection in Texas map
    select_county
)

# 0 percent line
line = alt.Chart(pd.DataFrame({'y': [0]})).mark_rule().encode(y='y')

unemployment_chart = alt.Chart(df).mark_line().encode(
    y = alt.Y('Unemployment Rate:Q', scale = alt.Scale(domain = [0,20])),
    x = alt.X('Time:Q', title = 'Year',
          # remove coma in year format
          axis = alt.Axis(format = 'd'),
          scale = alt.Scale(domain = [2000,2020])),
    color = 'County Name',
).properties(
    title = "Unemployment Rate of Selected Counties Over Time"
).transform_filter(
    select_county
)

df_rank = pd.read_excel("/cost_of_living_tx1.xlsx")
county = alt.selection_multi(fields=['County Name'], empty= 'none')
scatter = alt.Chart(df_rank).mark_point().encode(
    x = 'Median Home Value:Q',
    y = 'Median Rent:Q',
    size = alt.Size(type = 'quantitative', field = 'Population, 2021', scale = alt.Scale(range = [4, 500], bins = [0, 50000, 200000, 500000, 900000, 3000000])),
    color = alt.condition(select_county, alt.value('orange'), alt.value('purple')),
    tooltip = ['County Name', 'Ranking:N', 'Median Home Value', 'Median Rent']
).properties(
    title = 'Distribution of Cost of Living in Texas'
).add_selection(
    # fix tooltip bug
    alt.selection_single()
).interactive()

bar = alt.Chart(df_rank).mark_point().encode(
    x = alt.X('% Own:Q', scale = alt.Scale(domain = [0,100])),
    y = alt.Y('% Rent:Q', scale = alt.Scale(domain = [0,100])),
    tooltip = ['County Name:N', '% Rent', '% Own']
).properties(
    title = 'Rent vs. Own Distribution'
).transform_filter(
    select_county
).add_selection(
    # fix tooltip bug
    alt.selection_single()
).interactive()

In [ ]:
# Combine All Charts
(((texas_map) & ((base.mark_point().encode(tooltip = ['County Name', 'Growth Diff']).add_selection(alt.selection_single()) + base.mark_line() + line) | unemployment_chart)) | (scatter & bar)).save('chart.html')
((texas_map) & ((base.mark_point().encode(tooltip = ['County Name', 'Growth Diff']).add_selection(alt.selection_single()) + base.mark_line() + line) | unemployment_chart)) | (scatter & bar)



alt.HConcatChart(...)

In [ ]:
# county income vs state income
df_tp = pd.read_csv('/TXPCPI.csv')
df_tp.reset_index(drop=True, inplace=True)
df_c = df.drop(columns=['Housing Price Index', "Housing Price Growth", "gid", "Growth Diff", "2020 Population"])
df_tp = df_tp.iloc[72: , :]
names = df_c.drop(columns=["Unnamed: 0", "Unemployment Rate", "Income Growth", "Income", "Time"]).values.tolist()
flat_names = sorted(list(set([item for sub in names for item in sub])))
df_c['Average Texas Income'] = df_tp.iloc[:, -1]
input_dropdown = alt.binding_select(options=flat_names)
selection = alt.selection_single(fields=['County Name'], bind=input_dropdown, name=' ')
color = alt.condition(selection,
                    alt.Color('County Name:N', legend=None),
                    alt.value('lightgray'))
scatter = alt.Chart(df_c).mark_line().encode(
    x = 'Time:O',
    y = 'Income:Q',
    color = color,
    tooltip = ["County Name"],
    size=alt.value(5)
).add_selection(
    selection
).transform_filter(
    selection
)
avg = alt.Chart(df_c).mark_line().encode(
    x = 'Time:O',
    y = 'Average Texas Income:Q',
    color=alt.condition(selection,
                    alt.Color('County Name:N', legend=None),
                    alt.value('blue')),
    tooltip = ["Average Texas Income"],
    size=alt.value(5)
)

avg + scatter







alt.LayerChart(...)